# Multimodal RAG Pipeline with LangChain + Ollama + Unstructured

## Building a RAG System with Open-Source Tools

This notebook is my attempt at building a multimodal RAG pipeline using some open-source tools I've been experimenting with.

### What I'm Using:
- **LangChain** - for orchestrating everything
- **Ollama** - running LLMs locally (no API costs!)
- **Unstructured** - parsing PDFs, tables, images etc.
- **ChromaDB** - vector storage
- **MultiVectorRetriever** - handles both summaries and raw docs

### What it does:
- Extracts text, tables, and images from PDFs
- Summarizes each element for better retrieval
- Stores summaries in vector DB, keeps raw content separate
- Retrieves relevant context and generates answers
- Everything runs locally - no cloud APIs needed!
- Can process multiple PDFs at once with source tracking
- Query specific documents or search across all of them
- Compare info between different documents
- Add new PDFs incrementally without reprocessing everything


This is the full workflow intended:

system.png

## Step 0: Install Dependencies

First things first, let's get all the packages installed.


In [1]:
# Installing everything we need
%pip install -q langchain langchain-community langchain-ollama
%pip install -q chromadb
%pip install -q "unstructured[all-docs]" python-magic
%pip install -q pillow pdf2image pdfminer-six
%pip install -q pandas openpyxl tabulate
%pip install -q pytesseract


Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorboard 2.15.1 requires protobuf<4.24,>=3.19.6, but you have protobuf 6.32.1 which is incompatible.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [2]:
# Had some issues with numpy compatibility, so forcing reinstall here
%pip install --force-reinstall numpy pandas scikit-learn

  Using cached numpy-2.3.3-cp312-cp312-manylinux_2_27_x86_64.manylinux_2_28_x86_64.whl.metadata (62 kB)
  Using cached pandas-2.3.3-cp312-cp312-manylinux_2_24_x86_64.manylinux_2_28_x86_64.whl.metadata (91 kB)
  Using cached scikit_learn-1.7.2-cp312-cp312-manylinux2014_x86_64.manylinux_2_17_x86_64.whl.metadata (11 kB)
  Using cached python_dateutil-2.9.0.post0-py2.py3-none-any.whl.metadata (8.4 kB)
  Using cached pytz-2025.2-py2.py3-none-any.whl.metadata (22 kB)
  Using cached tzdata-2025.2-py2.py3-none-any.whl.metadata (1.4 kB)
  Using cached scipy-1.16.2-cp312-cp312-manylinux2014_x86_64.manylinux_2_17_x86_64.whl.metadata (62 kB)
  Using cached joblib-1.5.2-py3-none-any.whl.metadata (5.6 kB)
  Using cached threadpoolctl-3.6.0-py3-none-any.whl.metadata (13 kB)
  Using cached six-1.17.0-py2.py3-none-any.whl.metadata (1.7 kB)
Using cached numpy-2.3.3-cp312-cp312-manylinux_2_27_x86_64.manylinux_2_28_x86_64.whl (16.6 MB)
Using cached pandas-2.3.3-cp312-cp312-manylinux_2_24_x86_64.manylinux_

Also for Unstructured library, you should donwload these packages too:

In [3]:
!sudo apt-get install poppler-utils tesseract-ocr

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
poppler-utils is already the newest version (24.02.0-1ubuntu9.7).
tesseract-ocr is already the newest version (5.3.4-1build5).
0 upgraded, 0 newly installed, 0 to remove and 12 not upgraded.


## Quick Start Guide

### For a single PDF:
```python
pdf_path = "paper.pdf"
use_batch_mode = False
```

### For multiple PDFs:
```python
pdf_paths = [
    "paper1.pdf",
    "paper2.pdf",
    "research_doc.pdf"
]
use_batch_mode = True
```

### Features I added:
- Process multiple PDFs at once
- Track which PDF each piece of info came from
- Query specific documents or all at once
- Add new PDFs later without starting over
- Compare information across different sources

Check out Step 4 to set up your PDF paths!


## Prerequisites: Setting Up Ollama

Before running this notebook, you need to get Ollama set up.

### 1. Install Ollama
Grab it from: **https://ollama.ai/download**

### 2. Start the Ollama Server
```bash
ollama serve
```

### 3. Download the models we'll use
```bash
# Main model for text generation
ollama pull gemma3:4b

# Embeddings model (smaller, faster)
ollama pull embeddinggemma:300m:

# Optional: if you want vision capabilities
ollama pull llava:7b
```

### 4. Make sure it worked
```bash
ollama list
```


## Step 1: Import Libraries and Check Ollama Connection


In [4]:
import os
import uuid
import base64
from pathlib import Path
from typing import List, Dict, Any
import warnings
warnings.filterwarnings('ignore')

# LangChain stuff
from langchain_ollama import ChatOllama, OllamaEmbeddings
from langchain_community.vectorstores import Chroma
from langchain.storage import InMemoryStore
from langchain.schema.document import Document
from langchain.retrievers.multi_vector import MultiVectorRetriever
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough

# Unstructured for PDF parsing
from unstructured.partition.pdf import partition_pdf
from unstructured.partition.auto import partition

# Other utilities
import pandas as pd
from IPython.display import Image as IPImage, display, HTML
import requests

print("All imports successful!")


All imports successful!


In [5]:
# Let's check if Ollama is running
def test_ollama():
    """Quick test to see if Ollama is up and what models are available"""
    try:
        response = requests.get("http://localhost:11434/api/tags", timeout=5)
        if response.status_code == 200:
            models = response.json().get('models', [])
            print("✓ Ollama is running!")
            print(f"✓ Found {len(models)} models:\n")
            for model in models:
                print(f"  • {model['name']}")
                print(f"    Size: {model.get('size', 0) / 1e9:.2f} GB\n")
            return True
        else:
            print(f"✗ Ollama returned status: {response.status_code}")
            return False
    except Exception as e:
        print(f"✗ Could not connect to Ollama: {e}")
        print("\nMake sure you:")
        print("  1. Installed Ollama from https://ollama.ai/download")
        print("  2. Started the server: ollama serve")
        print("  3. Pulled some models: ollama pull llama3.1:8b")
        return False

test_ollama()


✗ Could not connect to Ollama: HTTPConnectionPool(host='localhost', port=11434): Max retries exceeded with url: /api/tags (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x7c78d4f90b30>: Failed to establish a new connection: [Errno 111] Connection refused'))

Make sure you:
  1. Installed Ollama from https://ollama.ai/download
  2. Started the server: ollama serve
  3. Pulled some models: ollama pull llama3.1:8b


False

## Step 2: Initialize the Models


In [6]:
# Setting up the main LLM
llm = ChatOllama(
    model="gemma3:4b",  # it's pretty fast
    temperature=0.2,    # keeping it focused just on docs 
)

# Embeddings model
embeddings = OllamaEmbeddings(
    model="embeddinggemma:300m",
)

print("LLM initialized: gemma3:4b")
print("Embeddings initialized: embeddinggemma:300m")
print("\nFeel free to change these models if you have others installed")


LLM initialized: gemma3:4b
Embeddings initialized: embeddinggemma:300m

Feel free to change these models if you have others installed


## Step 3: Setup Vector Store and MultiVectorRetriever

The MultiVectorRetriever lets us:
- Store summaries in the vector database (fast retrieval)
- Keep raw content separate (full context for the LLM)
- Retrieve using summaries but return complete content


In [7]:
# Setup vector store with ChromaDB
vectorstore = Chroma(
    collection_name="nasa_multimodal_rag",
    embedding_function=embeddings,
    persist_directory="./chroma_langchain_db"  # saves to disk
)

# In-memory store for the raw content
docstore = InMemoryStore()

# ID key for linking summaries to raw content
id_key = "doc_id"

# Create the retriever
retriever = MultiVectorRetriever(
    vectorstore=vectorstore,
    docstore=docstore,
    id_key=id_key,
)

print("Vector store initialized (ChromaDB)")
print("Document store initialized (In-Memory)")
print("MultiVectorRetriever ready")


/tmp/ipykernel_104859/1207277614.py:2: LangChainDeprecationWarning: The class `Chroma` was deprecated in LangChain 0.2.9 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-chroma package and should be used instead. To use it run `pip install -U :class:`~langchain-chroma` and import as `from :class:`~langchain_chroma import Chroma``.
  vectorstore = Chroma(


Vector store initialized (ChromaDB)
Document store initialized (In-Memory)
MultiVectorRetriever ready


## Find all PDFs in the folder


In [8]:
from pathlib import Path

# Grab all PDF files from the pdfs folder
pdfs = [str(p) for p in Path("../pdfs").glob("*.pdf")]

print(f"Found {len(pdfs)} PDF files:")
for path in pdfs:
    print(f"  - {path}")


Found 15 PDF files:
  - ../pdfs/PMC3040128.pdf
  - ../pdfs/PMC5387210.pdf
  - ../pdfs/PMC11500582.pdf
  - ../pdfs/PMC5460236.pdf
  - ../pdfs/PMC5587110.pdf
  - ../pdfs/PMC4136787.pdf
  - ../pdfs/PMC5666799.pdf
  - ../pdfs/PMC8396460.pdf
  - ../pdfs/PMC11988870.pdf
  - ../pdfs/PMC4095884.pdf
  - ../pdfs/PMC6222041.pdf
  - ../pdfs/PMC3630201.pdf
  - ../pdfs/PMC7998608.pdf
  - ../pdfs/PMC3177255.pdf
  - ../pdfs/PMC6813909.pdf


## Step 4: Parse PDFs with Unstructured

Unstructured is really powerful for this stuff:
- Parses PDFs accurately
- Extracts tables with structure preserved
- Grabs embedded images
- Works with lots of document formats


In [9]:
def load_and_parse_pdf(pdf_path: str):
    """
    Parse a PDF and extract text, tables, and images.
    Using Unstructured's partition_pdf function.
    """
    print(f"Processing: {pdf_path}")
    
    # Parse the PDF
    raw_pdf_elements = partition_pdf(
        filename=pdf_path,
        
        # Get tables
        infer_table_structure=True,
        
        # Use high-res processing for better quality
        strategy="hi_res",
        
        # Extract images from the PDF
        extract_images_in_pdf=True,
        extract_image_block_types=["Image", "Table"],
        extract_image_block_to_payload=True,
        
        # Chunking settings - these seem to work well
        chunking_strategy="by_title",
        max_characters=10000,
        combine_text_under_n_chars=2000,
        new_after_n_chars=6000,
    )
    
    print(f"Extracted {len(raw_pdf_elements)} elements from PDF\n")
    
    return raw_pdf_elements

def process_multiple_pdfs(pdf_paths: List[str]):
    """
    Process a bunch of PDFs at once and track where each element came from.
    
    Returns a dict with filename as key and elements as value.
    """
    all_pdf_elements = {}
    
    print(f"Processing {len(pdf_paths)} PDF files...\n")
    print("="*80)
    
    for pdf_path in pdf_paths:
        if Path(pdf_path).exists():
            try:
                elements = load_and_parse_pdf(pdf_path)
                filename = Path(pdf_path).name
                all_pdf_elements[filename] = elements
                print(f"Successfully processed: {filename}")
                print(f"  Elements extracted: {len(elements)}\n")
            except Exception as e:
                print(f"Error processing {pdf_path}: {e}\n")
        else:
            print(f"File not found: {pdf_path}\n")

    print("="*80)
    print(f"\nTotal PDFs processed: {len(all_pdf_elements)}")
    total_elements = sum(len(elements) for elements in all_pdf_elements.values())
    print(f"Total elements extracted: {total_elements}\n")

    return all_pdf_elements

# Change this to your PDF file
pdf_path = "paper.pdf"

# Or use multiple PDFs like this
pdf_paths = pdfs

# Toggle between single and batch mode
use_batch_mode = True  # set to False for just one PDF

if use_batch_mode:
    # Process multiple PDFs
    all_elements_by_source = process_multiple_pdfs(pdf_paths)
    
    # Flatten everything and add source metadata
    elements = []
    for source, source_elements in all_elements_by_source.items():
        for elem in source_elements:
            if hasattr(elem, 'metadata'):
                elem.metadata.source_file = source
            elements.append(elem)
    
    if elements:
        print(f"Element types: {set([str(type(el).__name__) for el in elements])}")
else:
    # Process just one PDF
    if Path(pdf_path).exists():
        elements = load_and_parse_pdf(pdf_path)
        # Add source metadata
        for elem in elements:
            if hasattr(elem, 'metadata'):
                elem.metadata.source_file = Path(pdf_path).name
        all_elements_by_source = {Path(pdf_path).name: elements}
        print(f"Element types: {set([str(type(el).__name__) for el in elements])}")
    else:
        print(f"File not found: {pdf_path}")
        print("Update the pdf_path variable with your PDF file")
        elements = []
        all_elements_by_source = {}


Processing 15 PDF files...

Processing: ../pdfs/PMC3040128.pdf


preprocessor_config.json:   0%|          | 0.00/274 [00:00<?, ?B/s]

The `max_size` parameter is deprecated and will be removed in v4.26. Please specify in `size['longest_edge'] instead`.


config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/115M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/46.8M [00:00<?, ?B/s]

Extracted 12 elements from PDF

Successfully processed: PMC3040128.pdf
  Elements extracted: 12

Processing: ../pdfs/PMC5387210.pdf
Extracted 14 elements from PDF

Successfully processed: PMC5387210.pdf
  Elements extracted: 14

Processing: ../pdfs/PMC11500582.pdf
Extracted 10 elements from PDF

Successfully processed: PMC11500582.pdf
  Elements extracted: 10

Processing: ../pdfs/PMC5460236.pdf
Extracted 12 elements from PDF

Successfully processed: PMC5460236.pdf
  Elements extracted: 12

Processing: ../pdfs/PMC5587110.pdf
Extracted 17 elements from PDF

Successfully processed: PMC5587110.pdf
  Elements extracted: 17

Processing: ../pdfs/PMC4136787.pdf
Extracted 19 elements from PDF

Successfully processed: PMC4136787.pdf
  Elements extracted: 19

Processing: ../pdfs/PMC5666799.pdf
Extracted 14 elements from PDF

Successfully processed: PMC5666799.pdf
  Elements extracted: 14

Processing: ../pdfs/PMC8396460.pdf
Extracted 13 elements from PDF

Successfully processed: PMC8396460.pdf
  E

## Step 5: Sort Elements by Type


In [10]:
def categorize_elements(raw_elements):
    """
    Split elements into text, tables, and images.
    Keeps source file metadata intact.
    """
    texts = []
    
    for element in raw_elements:
        element_type = str(type(element).__name__)
        
        if element_type == "CompositeElement":
            # Text element - keep the object to preserve metadata
            texts.append(element)
    
    return texts

# Extract tables from CompositeElements
def get_tables(chunks):
    tables = []
    for chunk in chunks:
        if "CompositeElement" in str(type(chunk)):
            chunk_els = chunk.metadata.orig_elements
            for el in chunk_els:
                if "Table" in str(type(el)):
                    source_file = getattr(chunk.metadata, 'source_file', 'unknown')
                    tables.append({
                        'content': el.metadata.text_as_html,
                        'source': source_file
                    })
    return tables

# Extract images from CompositeElements
def get_images_base64(chunks):
    images_b64 = []
    for chunk in chunks:
        if "CompositeElement" in str(type(chunk)):
            chunk_els = chunk.metadata.orig_elements
            for el in chunk_els:
                if "Image" in str(type(el)):
                    source_file = getattr(chunk.metadata, 'source_file', 'unknown')
                    images_b64.append({
                        'content': el.metadata.image_base64,
                        'source': source_file
                    })
    return images_b64

def filter_unknown_sources(texts, tables, images):
    """
    Remove elements with 'unknown' source - usually means something went wrong
    """
    # Filter texts
    filtered_texts = [
        text for text in texts 
        if hasattr(text, 'metadata') and 
        getattr(text.metadata, 'source_file', 'unknown') != 'unknown'
    ]
    
    # Filter tables
    filtered_tables = [
        table for table in tables 
        if isinstance(table, dict) and table.get('source', 'unknown') != 'unknown'
    ]
    
    # Filter images
    filtered_images = [
        image for image in images 
        if isinstance(image, dict) and image.get('source', 'unknown') != 'unknown'
    ]
    
    return filtered_texts, filtered_tables, filtered_images

if elements:
    texts = categorize_elements(elements)
    tables = get_tables(elements)
    images = get_images_base64(elements)
    
    print(f"Categorized elements (before filtering):")
    print(f"  Text chunks: {len(texts)}")
    print(f"  Tables: {len(tables)}")
    print(f"  Images: {len(images)}")
    
    # Clean up unknown sources
    texts, tables, images = filter_unknown_sources(texts, tables, images)
    
    print(f"\nAfter filtering out 'unknown' sources:")
    print(f"  Text chunks: {len(texts)}")
    print(f"  Tables: {len(tables)}")
    print(f"  Images: {len(images)}")
    
    # Show breakdown by source
    if all_elements_by_source:
        print(f"\nBreakdown by source file:")
        for source, source_elements in all_elements_by_source.items():
            source_texts = categorize_elements(source_elements)
            source_tables = get_tables(source_elements)
            source_images = get_images_base64(source_elements)
            # Filter each source
            source_texts, source_tables, source_images = filter_unknown_sources(
                source_texts, source_tables, source_images
            )
            print(f"  {source}:")
            print(f"    - Text chunks: {len(source_texts)}")
            print(f"    - Tables: {len(source_tables)}")
            print(f"    - Images: {len(source_images)}")
else:
    texts, tables, images = [], [], []
    print("No elements to categorize")


Categorized elements (before filtering):
  Text chunks: 213
  Tables: 28
  Images: 184

After filtering out 'unknown' sources:
  Text chunks: 213
  Tables: 28
  Images: 184

Breakdown by source file:
  PMC3040128.pdf:
    - Text chunks: 12
    - Tables: 2
    - Images: 44
  PMC5387210.pdf:
    - Text chunks: 14
    - Tables: 0
    - Images: 9
  PMC11500582.pdf:
    - Text chunks: 10
    - Tables: 0
    - Images: 6
  PMC5460236.pdf:
    - Text chunks: 12
    - Tables: 2
    - Images: 4
  PMC5587110.pdf:
    - Text chunks: 17
    - Tables: 3
    - Images: 25
  PMC4136787.pdf:
    - Text chunks: 19
    - Tables: 6
    - Images: 12
  PMC5666799.pdf:
    - Text chunks: 14
    - Tables: 3
    - Images: 23
  PMC8396460.pdf:
    - Text chunks: 13
    - Tables: 2
    - Images: 6
  PMC11988870.pdf:
    - Text chunks: 16
    - Tables: 1
    - Images: 6
  PMC4095884.pdf:
    - Text chunks: 15
    - Tables: 0
    - Images: 9
  PMC6222041.pdf:
    - Text chunks: 12
    - Tables: 2
    - Images: 9
  

## Step 6: Generate Summaries

Creating summaries for everything:
- Text chunks → concise summaries
- Tables → describe structure and content
- Images → use vision model


In [11]:
# Prompt for summarizing text and tables
prompt_text = """
You are an assistant tasked with summarizing tables and text.
Give a concise comprehensive summary of the table or text.

Respond only with the summary, no additional comment.
Do not start your message by saying "Here is a summary" or anything like that.
Just give the summary as it is.

HTML Table or text chunk: {element}

"""
prompt = ChatPromptTemplate.from_template(prompt_text)

# Summarization chain
model = ChatOllama(temperature=0.2, model="gemma3:4b")
summarize_chain = {"element": lambda x: x} | prompt | model | StrOutputParser()

print("Text and table summarization chain ready")

# Prompt for describing images
prompt_template = """Describe the image in detail. For context,
                  the image is part of a research paper. Be specific about graphs, such as bar plots."""
messages = [
    (
        "user",
        [
            {"type": "text", "text": prompt_template},
            {
                "type": "image_url",
                "image_url": {"url": "data:image/jpeg;base64,{image}"},
            },
        ],
    )
]

image_prompt = ChatPromptTemplate.from_messages(messages)

# Image description chain using llava
image_chain = image_prompt | ChatOllama(model="llava:7b") | StrOutputParser()

print("Image description chain ready")


Text and table summarization chain ready
Image description chain ready


In [13]:
# Generate summaries - using batch processing to speed things up
print("Generating summaries...\n")

text_summaries = []
table_summaries = []
image_summaries = []

# Summarize text chunks
if texts:
    print(f"Summarizing {len(texts)} text chunks...")
    # Extract text content from objects
    text_contents = [text_elem.text if hasattr(text_elem, 'text') else str(text_elem) for text_elem in texts]
    text_summaries = summarize_chain.batch(text_contents, {"max_concurrency": 3})
    print(f"Generated {len(text_summaries)} text summaries")

# Summarize tables
if tables:
    print(f"Summarizing {len(tables)} tables...")
    table_contents = [table_dict['content'] if isinstance(table_dict, dict) else table_dict for table_dict in tables]
    table_summaries = summarize_chain.batch(table_contents, {"max_concurrency": 3})
    print(f"Generated {len(table_summaries)} table summaries")

# Describe images
if images:
    print(f"Describing {len(images)} images...")
    try:
        image_contents = [image_dict['content'] if isinstance(image_dict, dict) else image_dict for image_dict in images]
        image_summaries = image_chain.batch(image_contents)
        print(f"Generated {len(image_summaries)} image summaries")
    except Exception as e:
        print(f"Error with vision model: {e}")
        print("Using placeholder descriptions instead...")
        image_summaries = [f"Image content (vision model not available)" for _ in images]

print(f"\nSummarization complete!")
print(f"   Total summaries: {len(text_summaries) + len(table_summaries) + len(image_summaries)}")


Generating summaries...

Summarizing 213 text chunks...


Generated 213 text summaries
Summarizing 28 tables...
Generated 28 table summaries
Describing 184 images...
Generated 184 image summaries

Summarization complete!
   Total summaries: 425


## Step 7: Add Everything to the Retriever

Store summaries in vector store (for searching) and raw content in document store (for LLM context)


In [14]:
def add_documents_to_retriever(texts, text_summaries, tables, table_summaries, images, image_summaries):
    """
    Add all documents to the MultiVectorRetriever.
    Includes source file metadata for tracking which PDF each piece came from.
    """
    
    # Add text documents
    text_ids = [str(uuid.uuid4()) for _ in texts]
    
    if texts:
        # Store summaries in vector store
        summary_docs = []
        for i, (text_elem, summary) in enumerate(zip(texts, text_summaries)):
            source_file = getattr(text_elem.metadata, 'source_file', 'unknown') if hasattr(text_elem, 'metadata') else 'unknown'
            summary_docs.append(
                Document(
                    page_content=summary, 
                    metadata={
                        id_key: text_ids[i], 
                        "type": "text",
                        "source_file": source_file
                    }
                )
            )
        retriever.vectorstore.add_documents(summary_docs)
        
        # Store raw content separately
        text_contents = [elem.text if hasattr(elem, 'text') else str(elem) for elem in texts]
        retriever.docstore.mset(list(zip(text_ids, text_contents)))
        print(f"Added {len(texts)} text documents")
    
    # Add table documents
    table_ids = [str(uuid.uuid4()) for _ in tables]
    
    if tables:
        # Store summaries
        summary_docs = []
        for i, (table_dict, summary) in enumerate(zip(tables, table_summaries)):
            source_file = table_dict.get('source', 'unknown') if isinstance(table_dict, dict) else 'unknown'
            summary_docs.append(
                Document(
                    page_content=summary,
                    metadata={
                        id_key: table_ids[i],
                        "type": "table",
                        "source_file": source_file
                    }
                )
            )
        retriever.vectorstore.add_documents(summary_docs)
        
        # Store raw HTML tables
        table_contents = [t['content'] if isinstance(t, dict) else t for t in tables]
        retriever.docstore.mset(list(zip(table_ids, table_contents)))
        print(f"Added {len(tables)} table documents")
    
    # Add image documents
    image_ids = [str(uuid.uuid4()) for _ in images]
    
    if images:
        # Store descriptions
        summary_docs = []
        for i, (image_dict, summary) in enumerate(zip(images, image_summaries)):
            source_file = image_dict.get('source', 'unknown') if isinstance(image_dict, dict) else 'unknown'
            summary_docs.append(
                Document(
                    page_content=summary,
                    metadata={
                        id_key: image_ids[i],
                        "type": "image",
                        "source_file": source_file
                    }
                )
            )
        retriever.vectorstore.add_documents(summary_docs)
        
        # Store base64 image data
        image_contents = [img['content'] if isinstance(img, dict) else img for img in images]
        retriever.docstore.mset(list(zip(image_ids, image_contents)))
        print(f"Added {len(images)} image documents")
    
    # Show stats by source file
    if texts or tables or images:
        print("\nAll documents added to retriever!")
        print("\nDocuments by source file:")
        
        # Collect stats
        source_stats = {}
        
        # Count texts
        for text_elem in texts:
            source = getattr(text_elem.metadata, 'source_file', 'unknown') if hasattr(text_elem, 'metadata') else 'unknown'
            source_stats[source] = source_stats.get(source, {'texts': 0, 'tables': 0, 'images': 0})
            source_stats[source]['texts'] += 1
        
        # Count tables
        for table_dict in tables:
            source = table_dict.get('source', 'unknown') if isinstance(table_dict, dict) else 'unknown'
            source_stats[source] = source_stats.get(source, {'texts': 0, 'tables': 0, 'images': 0})
            source_stats[source]['tables'] += 1
        
        # Count images
        for image_dict in images:
            source = image_dict.get('source', 'unknown') if isinstance(image_dict, dict) else 'unknown'
            source_stats[source] = source_stats.get(source, {'texts': 0, 'tables': 0, 'images': 0})
            source_stats[source]['images'] += 1
        
        # Display
        for source, stats in source_stats.items():
            total = stats['texts'] + stats['tables'] + stats['images']
            print(f"  {source}: {total} documents")
            print(f"    - Texts: {stats['texts']}, Tables: {stats['tables']}, Images: {stats['images']}")
    
# Add everything to the retriever
if texts or tables or images:
    add_documents_to_retriever(texts, text_summaries, tables, table_summaries, images, image_summaries)
else:
    print("No documents to add")


Added 213 text documents
Added 28 table documents
Added 184 image documents

All documents added to retriever!

Documents by source file:
  PMC3040128.pdf: 58 documents
    - Texts: 12, Tables: 2, Images: 44
  PMC5387210.pdf: 23 documents
    - Texts: 14, Tables: 0, Images: 9
  PMC11500582.pdf: 16 documents
    - Texts: 10, Tables: 0, Images: 6
  PMC5460236.pdf: 18 documents
    - Texts: 12, Tables: 2, Images: 4
  PMC5587110.pdf: 45 documents
    - Texts: 17, Tables: 3, Images: 25
  PMC4136787.pdf: 37 documents
    - Texts: 19, Tables: 6, Images: 12
  PMC5666799.pdf: 40 documents
    - Texts: 14, Tables: 3, Images: 23
  PMC8396460.pdf: 21 documents
    - Texts: 13, Tables: 2, Images: 6
  PMC11988870.pdf: 23 documents
    - Texts: 16, Tables: 1, Images: 6
  PMC4095884.pdf: 24 documents
    - Texts: 15, Tables: 0, Images: 9
  PMC6222041.pdf: 23 documents
    - Texts: 12, Tables: 2, Images: 9
  PMC3630201.pdf: 30 documents
    - Texts: 19, Tables: 4, Images: 7
  PMC7998608.pdf: 23 documen

## Step 8: 

Setting up the LangChain RAG pipeline:
1. Retrieves relevant documents
2. Formats the context
3. Generates answers based on retrieved info


In [15]:
# Prompt template for the RAG chain
template = """
Answer the question based on the following context.
Don't cite any sources in your response.
Don't say "Based on the resource" or any other simialar sentences.
Respond with Markdown format.

Context:
{context}

Question: {question}

Answer:
"""

prompt = ChatPromptTemplate.from_template(template)

# Helper function to format docs
def format_docs(docs):
    """Format retrieved documents for the prompt"""
    formatted = []
    for i, doc in enumerate(docs):
        content = doc if isinstance(doc, str) else str(doc)
        formatted.append(f"[Source {i+1}]\n{content[:1000]}...\n")
    return "\n\n".join(formatted)

def format_docs_with_source(docs, metadata_list):
    """Format docs with source file info"""
    formatted = []
    for i, (doc, meta) in enumerate(zip(docs, metadata_list)):
        content = doc if isinstance(doc, str) else str(doc)
        source = meta.get('source_file', 'unknown') if meta else 'unknown'
        formatted.append(f"[Source {i+1} - from {source}]\n{content[:1000]}...\n")
    return "\n\n".join(formatted)

# Build the RAG chain
rag_chain = (
    {
        "context": retriever | format_docs,
        "question": RunnablePassthrough()
    }
    | prompt
    | llm
    | StrOutputParser()
)

print("RAG chain created!")
print("Ready to answer questions from multiple PDFs")


RAG chain created!
Ready to answer questions from multiple PDFs


In [16]:
def query(question: str, show_sources: bool = True):
    """Query the RAG system and optionally show which sources were used"""
    print(f"\nQuestion: {question}")
    print("="*80)
    
    # Get the answer
    answer = rag_chain.invoke(question)
    
    print(f"\nAnswer:\n{answer}")
    print("\n" + "="*80)
    
    # Show retrieved documents
    docs = retriever.get_relevant_documents(question)
    print(f"\nRetrieved {len(docs)} relevant documents")
    
    if show_sources:
        # Get metadata from vector store
        results = retriever.vectorstore.similarity_search(question, k=5)
        sources = {}
        for r in results:
            source = r.metadata.get('source_file', 'unknown')
            doc_type = r.metadata.get('type', 'unknown')
            if source not in sources:
                sources[source] = []
            sources[source].append(doc_type)
        
        print(f"\nSources used:")
        for source, types in sources.items():
            type_counts = {}
            for t in types:
                type_counts[t] = type_counts.get(t, 0) + 1
            type_str = ", ".join([f"{count} {type}" for type, count in type_counts.items()])
            print(f"  • {source}: {type_str}")
    
    return answer

## Step 9: Ask Questions!

Now we can query the system about our documents


In [17]:
# Let's try a query
query("what do you know about Mice experiments?")


Question: what do you know about Mice experiments?



Answer:
The provided sources detail several mouse experiments. Specifically, there are in vitro and in vivo studies involving different groups of mice, categorized as Flight experiment (SF), Flight vivarium control (SFV), Ground control experiment (GC), and Ground control experiment - vivarium control (GCV). These experiments involve varying measurements like force (in Newtons) and tissue area (in mm²). The data includes measurements from L4 and L5 specimens, with associated values for max force, max stress, tissue area, and other relevant metrics.


Retrieved 4 relevant documents


/tmp/ipykernel_104859/496191902.py:13: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 1.0. Use :meth:`~invoke` instead.
  docs = retriever.get_relevant_documents(question)



Sources used:
  • PMC7998608.pdf: 1 table
  • PMC4136787.pdf: 1 table
  • PMC8396460.pdf: 1 text
  • PMC6222041.pdf: 1 table
  • PMC3630201.pdf: 1 table


'The provided sources detail several mouse experiments. Specifically, there are in vitro and in vivo studies involving different groups of mice, categorized as Flight experiment (SF), Flight vivarium control (SFV), Ground control experiment (GC), and Ground control experiment - vivarium control (GCV). These experiments involve varying measurements like force (in Newtons) and tissue area (in mm²). The data includes measurements from L4 and L5 specimens, with associated values for max force, max stress, tissue area, and other relevant metrics.'

In [18]:
# Another query
query("What are the key findings or results or coclusions?")


Question: What are the key findings or results or coclusions?



Answer:
The table entries provide primer sequences for genes including ACTB, ocT4, SOX2, NANOG, MYC, KLP4, and cpa. The electrophoresis assay results show a significant decrease in fluorescence unit (FU) value at 150 kDa for the 17,000 Gy sample compared to the 0 Gy control, indicating collagen fragmentation.  Additionally, the data suggests a correlation between radiation dose (Gy) and vertebral strength, with increased AGEs (collagen crosslinks) and collagen fragmentation leading to a decrease in normalized vertebral strength. Gene list enrichment analysis (as described in Chen et al., 2009) could be used to identify candidate genes involved in these processes.


Retrieved 4 relevant documents

Sources used:
  • PMC7998608.pdf: 1 table
  • PMC3630201.pdf: 1 table
  • PMC6813909.pdf: 1 text
  • PMC8396460.pdf: 1 text
  • PMC11988870.pdf: 1 text


'The table entries provide primer sequences for genes including ACTB, ocT4, SOX2, NANOG, MYC, KLP4, and cpa. The electrophoresis assay results show a significant decrease in fluorescence unit (FU) value at 150 kDa for the 17,000 Gy sample compared to the 0 Gy control, indicating collagen fragmentation.  Additionally, the data suggests a correlation between radiation dose (Gy) and vertebral strength, with increased AGEs (collagen crosslinks) and collagen fragmentation leading to a decrease in normalized vertebral strength. Gene list enrichment analysis (as described in Chen et al., 2009) could be used to identify candidate genes involved in these processes.'

In [19]:
# Custom question
query("What are the experiments performed on mice?")


Question: What are the experiments performed on mice?



Answer:
The experiments performed on mice include a Flight experiment (SF) with 11 in vitro studies and 5 in vivo studies, a Flight vivarium control experiment (SFV) with 18 in vitro studies and 20 in vivo studies, and a Ground control experiment (GC) with 16 in vitro studies and 9 in vivo studies. Additionally, a Ground control experiment - vivarium control (GCV) was performed with 16 in vitro studies and 13 in vivo studies.



Retrieved 4 relevant documents

Sources used:
  • PMC4136787.pdf: 1 table
  • PMC7998608.pdf: 1 table
  • PMC3630201.pdf: 1 table
  • PMC8396460.pdf: 1 text
  • PMC5587110.pdf: 1 table


'The experiments performed on mice include a Flight experiment (SF) with 11 in vitro studies and 5 in vivo studies, a Flight vivarium control experiment (SFV) with 18 in vitro studies and 20 in vivo studies, and a Ground control experiment (GC) with 16 in vitro studies and 9 in vivo studies. Additionally, a Ground control experiment - vivarium control (GCV) was performed with 16 in vitro studies and 13 in vivo studies.\n'

# Exporting the databases for the backend team

In [22]:
import csv
import json
import numpy as np
from datetime import datetime

def export_chroma_to_csv(output_file: str = "chroma_export.csv"):
    """
    Export ChromaDB contents to CSV for PostgreSQL/pgvector import.
    
    Exports document IDs, content, embeddings, and metadata.
    """
    print(f"Exporting ChromaDB to {output_file}...")
    print("="*80)
    
    try:
        # Get all documents from vectorstore
        collection = retriever.vectorstore._collection
        
        # Fetch everything
        results = collection.get(
            include=['embeddings', 'documents', 'metadatas']
        )
        
        # Prepare data for CSV
        rows = []
        for i in range(len(results['ids'])):
            # Convert embedding to list if needed
            embedding = results['embeddings'][i]
            if isinstance(embedding, np.ndarray):
                embedding = embedding.tolist()
            elif not isinstance(embedding, list):
                embedding = list(embedding)
            
            row = {
                'id': results['ids'][i],
                'content': results['documents'][i],
                'embedding': json.dumps(embedding),  # serialize to JSON
                'metadata': json.dumps(results['metadatas'][i]),
                'doc_type': results['metadatas'][i].get('type', 'unknown'),
                'source_file': results['metadatas'][i].get('source_file', 'unknown'),
                'doc_id': results['metadatas'][i].get(id_key, ''),
                'created_at': datetime.now().isoformat()
            }
            rows.append(row)
        
        # Write to CSV
        if rows:
            fieldnames = ['id', 'content', 'embedding', 'metadata', 'doc_type', 
                         'source_file', 'doc_id', 'created_at']
            
            with open(output_file, 'w', newline='', encoding='utf-8') as f:
                writer = csv.DictWriter(f, fieldnames=fieldnames, quoting=csv.QUOTE_MINIMAL)
                writer.writeheader()
                writer.writerows(rows)
            
            print(f"Exported {len(rows)} documents to {output_file}")
            
            # Check embedding dimension
            if rows:
                first_embedding = json.loads(rows[0]['embedding'])
                print(f"Embedding dimension: {len(first_embedding)}")
            
            print(f"\nFile structure:")
            print(f"  - id: Unique document identifier")
            print(f"  - content: Document summary text")
            print(f"  - embedding: Vector embedding (JSON array)")
            print(f"  - metadata: Full metadata (JSON)")
            print(f"  - doc_type: Type (text/table/image)")
            print(f"  - source_file: Original PDF filename")
            print(f"  - doc_id: Link to raw content")
            print(f"  - created_at: Export timestamp")
            
            # Show some stats
            by_type = {}
            by_source = {}
            for row in rows:
                doc_type = row['doc_type']
                source = row['source_file']
                by_type[doc_type] = by_type.get(doc_type, 0) + 1
                by_source[source] = by_source.get(source, 0) + 1
            
            print(f"\nExport Statistics:")
            print(f"  Total documents: {len(rows)}")
            print(f"  By type: {by_type}")
            print(f"  By source: {by_source}")
            
        else:
            print("No documents found in ChromaDB")
            
    except Exception as e:
        print(f"✗ Error exporting: {e}")
        import traceback
        traceback.print_exc()

def export_raw_content_to_csv(output_file: str = "raw_content_export.csv"):
    """
    Export raw document content from docstore to CSV.
    This includes full text/tables/images that aren't in the vector DB.
    """
    print(f"Exporting raw content to {output_file}...")
    print("="*80)
    
    try:
        # Get doc_ids from vectorstore
        collection = retriever.vectorstore._collection
        results = collection.get(include=['metadatas'])
        
        doc_ids = [meta.get(id_key) for meta in results['metadatas'] if meta.get(id_key)]
        
        # Get raw content from docstore
        raw_contents = retriever.docstore.mget(doc_ids)
        
        # Prepare CSV data
        rows = []
        for doc_id, content in zip(doc_ids, raw_contents):
            if content:
                # Find metadata
                meta = next((m for m in results['metadatas'] if m.get(id_key) == doc_id), {})
                
                # Handle different content types
                content_str = content
                if isinstance(content, bytes):
                    # Encode binary content (images) as base64
                    import base64
                    content_str = base64.b64encode(content).decode('utf-8')
                elif not isinstance(content, str):
                    content_str = str(content)
                
                row = {
                    'doc_id': doc_id,
                    'content': content_str,
                    'doc_type': meta.get('type', 'unknown'),
                    'source_file': meta.get('source_file', 'unknown'),
                    'created_at': datetime.now().isoformat()
                }
                if row['source_file'] != 'unknown':
                    rows.append(row)
        
        # Write to CSV
        if rows:
            fieldnames = ['doc_id', 'content', 'doc_type', 'source_file', 'created_at']
            
            with open(output_file, 'w', newline='', encoding='utf-8') as f:
                writer = csv.DictWriter(f, fieldnames=fieldnames, quoting=csv.QUOTE_MINIMAL)
                writer.writeheader()
                writer.writerows(rows)

            print(f"Exported {len(rows)} raw documents to {output_file}")
            print(f"\nFile structure:")
            print(f"  - doc_id: Links to main export")
            print(f"  - content: Full raw content")
            print(f"  - doc_type: Type (text/table/image)")
            print(f"  - source_file: Original PDF filename")
            print(f"  - created_at: Export timestamp")
            
            # Show content size stats
            total_size = sum(len(row['content']) for row in rows)
            avg_size = total_size / len(rows) if rows else 0
            print(f"\nContent Statistics:")
            print(f"  Total characters: {total_size:,}")
            print(f"  Average size: {avg_size:,.0f} chars")
            
        else:
            print("No raw content found in docstore")
            
    except Exception as e:
        print(f"Error exporting raw content: {e}")
        import traceback
        traceback.print_exc()

def export_complete_dataset(base_name: str = "nasa_rag_export"):
    """
    Export both vectors and raw content in one go.
    Creates two CSV files that can be imported together.
    """
    print("Exporting Complete Dataset")
    print("="*80 + "\n")
    
    # Export vectors
    vectors_file = f"{base_name}_vectors.csv"
    export_chroma_to_csv(vectors_file)
    
    print("\n")
    
    # Export raw content
    content_file = f"{base_name}_content.csv"
    export_raw_content_to_csv(content_file)
    
    print("\n" + "="*80)
    print("Export complete!")
    print(f"\nFiles created:")
    print(f"  1. {vectors_file} - Vector embeddings and summaries")
    print(f"  2. {content_file} - Raw document content")


In [23]:
# Export everything
if texts or tables or images:
    export_complete_dataset("nasa_rag_export")
else:
    print("No documents to export - process some PDFs first")

Exporting Complete Dataset

Exporting ChromaDB to nasa_rag_export_vectors.csv...


Exported 425 documents to nasa_rag_export_vectors.csv
Embedding dimension: 768

File structure:
  - id: Unique document identifier
  - content: Document summary text
  - embedding: Vector embedding (JSON array)
  - metadata: Full metadata (JSON)
  - doc_type: Type (text/table/image)
  - source_file: Original PDF filename
  - doc_id: Link to raw content
  - created_at: Export timestamp

Export Statistics:
  Total documents: 425
  By type: {'text': 213, 'table': 28, 'image': 184}
  By source: {'PMC3040128.pdf': 58, 'PMC5387210.pdf': 23, 'PMC11500582.pdf': 16, 'PMC5460236.pdf': 18, 'PMC5587110.pdf': 45, 'PMC4136787.pdf': 37, 'PMC5666799.pdf': 40, 'PMC8396460.pdf': 21, 'PMC11988870.pdf': 23, 'PMC4095884.pdf': 24, 'PMC6222041.pdf': 23, 'PMC3630201.pdf': 30, 'PMC7998608.pdf': 23, 'PMC3177255.pdf': 25, 'PMC6813909.pdf': 19}


Exporting raw content to nasa_rag_export_content.csv...
Exported 425 raw documents to nasa_rag_export_content.csv

File structure:
  - doc_id: Links to main export
  - c